## Decorators

A common pattern in functional programs, are functions that are built to "wrap" other functions.

Functions are in fact mutable.

In [1]:
def print_before_and_after(func):
    def newfunc(*args, **kwargs):
        print("BEFORE", func)
        func(*args, **kwargs)
        print("AFTER", func)
    return newfunc

In [2]:
def inner():
    print("inner function")

In [3]:
wrapped_inner = print_before_and_after(inner)

wrapped_inner()
#print(x)

BEFORE <function inner at 0x1038697e0>
inner function
AFTER <function inner at 0x1038697e0>


In [4]:
# often we want to just replace the function altogether
# with the modified version
inner = print_before_and_after(inner)
inner()

BEFORE <function inner at 0x1038697e0>
inner function
AFTER <function inner at 0x1038697e0>


In [5]:
# another way of writing this is to use decorator syntax
@print_before_and_after
@print_before_and_after
def add_nums(a, b, c):
    print(f"{a} + {b} + {c} =", a + b + c)
#add_nums = print_before_and_after(print_before_and_after(add_nums))

In [6]:
add_nums(1, 2, 3)

BEFORE <function print_before_and_after.<locals>.newfunc at 0x10386a0e0>
BEFORE <function add_nums at 0x10386a050>
1 + 2 + 3 = 6
AFTER <function add_nums at 0x10386a050>
AFTER <function print_before_and_after.<locals>.newfunc at 0x10386a0e0>


In [7]:
def cache(func):
    inner_cache = {}
    
    def newfunc(*args, **kwargs):
        if args not in inner_cache:
            # will not work correctly if there are kwargs
            inner_cache[args] = func(*args, **kwargs)
        return inner_cache[args]
    
    return newfunc

In [8]:
@cache
def expensive_calculation(a, b):
    print(f"doing expensive calculation on {a} {b}...")
    return a ** b

@cache
def cheap_calculation(a, b):
    print(f"doing cheap calculation on {a} {b}...")
    return a + b

In [9]:
expensive_calculation(4, 10)

doing expensive calculation on 4 10...


1048576

In [10]:
expensive_calculation(4, 10)

1048576

In [11]:
cheap_calculation(4, 10)

doing cheap calculation on 4 10...


14

In [12]:
expensive_calculation(5, 6)

doing expensive calculation on 5 6...


15625

In [13]:
cheap_calculation(4, 10)

14

In [14]:
expensive_calculation(5, 6)

15625

In [15]:
def repeat5(func):                     # the decorator   
    def newfunc(a, b, c):      # the inner function
        for i in range(5):
            print(a, b, c)
    return newfunc

@repeat5       # the wrapped function
def print_sum(*args):
    print(sum(args))

In [16]:
print_sum(1, 2, 3)

1 2 3
1 2 3
1 2 3
1 2 3
1 2 3


In [17]:
# to make a decorator that takes additional arguments
# you need to write a decorator factory function that returns decorators

def repeat(n):                                   # factory: takes integer, returns decorator
    def repeat_decorator(func):                  # decorator: takes function, returns function
        def newfunc(*args, **kwargs):            # inner function: takes ?, returns ?
            for i in range(n):
                func(*args, **kwargs)
        return newfunc
    return repeat_decorator

@repeat(10)
def print_backwards(s):
    print("backwards")

print_backwards("backwards")

backwards
backwards
backwards
backwards
backwards
backwards
backwards
backwards
backwards
backwards


In [18]:
repeat_10 = repeat(10)
print(repeat_10)
print_backwards = repeat_10(print_backwards)


<function repeat.<locals>.repeat_decorator at 0x1038a95a0>


In [19]:
# Example: writing our own `partial`
# https://docs.python.org/3/library/functools.html#functools.partial

In [20]:
import functools
print_hello_names = functools.partial(print, "Hello", sep=", ")

In [21]:
print_hello_names("Scott", "Paul", "Lauren")

Hello, Scott, Paul, Lauren


In [22]:
print_hello_names.args

('Hello',)

In [23]:
print_hello_names.keywords

{'sep': ', '}

In [24]:
print_hello_names.func

<function print>

In [25]:
# since functions are objects, we can attach arbitrary values to them
def wrapper(func):
    def newfunc(*args, **kwargs):
        return func(*args, **kwargs)
    # we can do whatever we like after defining newfunc, but before returning it
    newfunc.is_wrapped = True
    return newfunc

In [26]:
# property is assigned to all wrapped functions
@wrapper
def our_function():
    print("inside our function")

our_function.is_wrapped

True

In [27]:
def our_partial(func, /, *args, **keywords):
    def newfunc(*fargs, **fkeywords):
        newkeywords = {**keywords, **fkeywords}
        return func(*args, *fargs, **newkeywords)
    # assign these properties from within the closure
    newfunc.func = func
    newfunc.args = args
    newfunc.keywords = keywords
    return newfunc

In [28]:
print_hello_names2 = our_partial(print, "Hello", sep=", ")
print_hello_names2("Scott", "Paul", "Lauren")

Hello, Scott, Paul, Lauren


In [29]:
print_hello_names2.args

('Hello',)

In [30]:
print_hello_names2.keywords

{'sep': ', '}

In [31]:
print_hello_names2.func

<function print>